In [1]:
import os
os.chdir('..')
print(os.getcwd())

/workspace/rendering


In [2]:
import os
import numpy as np
from pathlib import Path
import torch
from torch import nn

In [3]:
bindata = {}
for fp in sorted(Path("data/ManipNetBIN2").iterdir()):
    # print(fp)
    bindata[fp.stem] = np.fromfile(fp, dtype=np.float32)
for k, v in bindata.items():
    print(k, v.shape)

os.chdir("data/ManipNetBIN")
print(os.getcwd())

Decoder_b0 (214,)
Decoder_w0 (328704,)
DenseRes0_b0 (1536,)
DenseRes0_w0 (2359296,)
DenseRes1_b0 (1536,)
DenseRes1_w0 (2359296,)
DenseRes2_b0 (1536,)
DenseRes2_w0 (2359296,)
DenseRes3_b0 (1536,)
DenseRes3_w0 (2359296,)
Encoder0_b0 (512,)
Encoder0_w0 (98304,)
Encoder1_b0 (512,)
Encoder1_w0 (172032,)
Encoder2_b0 (512,)
Encoder2_w0 (932864,)
Xmean (2350,)
Xstd (2350,)
Ymean (214,)
Ystd (214,)
/workspace/rendering/data/ManipNetBIN


In [4]:
import torch.nn.functional as F

class ResBlock(nn.Module):
    def __init__(self, in_vec, out_vec):
        super(ResBlock, self).__init__()
        self.FC0= nn.Linear(in_vec, out_vec)
        self.FC1 = nn.Linear(in_vec, out_vec)

    def __call__(self, H_zero):
        H_zero_ = F.relu(H_zero)
        H_one = self.FC0(H_zero_) + H_zero_
        H_one_ = F.relu(H_one)
        H_two = self.FC1(H_one_) + H_one_ + H_zero_
        return H_two

In [5]:
# 訓練に際して、可能であればGPU（cuda）を設定します。GPUが搭載されていない場合はCPUを使用します
device = "cuda:0" if torch.cuda.is_available() else "cpu"
print("Using {} device".format(device))

# modelを定義します
class NeuralNetwork(nn.Module):
    def __init__(self):
        super(NeuralNetwork, self).__init__()
        self.Encoder0= nn.Linear(192, 512)
        self.Encoder1 = nn.Linear(336, 512)
        self.Encoder2 = nn.Linear(1822, 512)
        self.DenseRes0 = ResBlock(1536, 1536)
        self.DenseRes1 = ResBlock(1536, 1536)
        self.Decoder = nn.Linear(1536, 214)

    def forward(self, pose, traj, sensor):
        pose_ = self.Encoder0(pose)
        traj_ = self.Encoder1(traj)
        sensor_ = self.Encoder2(sensor)
        out = torch.cat([pose_, traj_, sensor_], dim=-1)
        out = self.DenseRes0(out)
        out = self.DenseRes1(out)
        out = self.Decoder(out)
        return out

model = NeuralNetwork().to(device)
print(device)
print(model)
# model()
# print(model.device)
# for param in model.Encoder1.parameters():
#     print("encoder", param.shape)
# pose, traj, sensor = torch.zeros([1,192]).to(device), torch.zeros([1,336]).to(device), torch.zeros([1,1822]).to(device)
# y = model(pose, traj, sensor)

Using cuda:0 device
cuda:0
NeuralNetwork(
  (Encoder0): Linear(in_features=192, out_features=512, bias=True)
  (Encoder1): Linear(in_features=336, out_features=512, bias=True)
  (Encoder2): Linear(in_features=1822, out_features=512, bias=True)
  (DenseRes0): ResBlock(
    (FC0): Linear(in_features=1536, out_features=1536, bias=True)
    (FC1): Linear(in_features=1536, out_features=1536, bias=True)
  )
  (DenseRes1): ResBlock(
    (FC0): Linear(in_features=1536, out_features=1536, bias=True)
    (FC1): Linear(in_features=1536, out_features=1536, bias=True)
  )
  (Decoder): Linear(in_features=1536, out_features=214, bias=True)
)


In [10]:
getbinname = {
    "Decoder.weight": "Decoder_w0",
    "Decoder.bias": "Decoder_b0",
    "Encoder0.weight": "Encoder0_w0",
    "Encoder0.bias": "Encoder0_b0",
    "Encoder1.weight": "Encoder1_w0",
    "Encoder1.bias": "Encoder1_b0",
    "Encoder2.weight": "Encoder2_w0",
    "Encoder2.bias": "Encoder2_b0",
    "DenseRes0.FC0.weight": "DenseRes0_w0",
    "DenseRes0.FC0.bias": "DenseRes0_b0",
    "DenseRes0.FC1.weight": "DenseRes1_w0",
    "DenseRes0.FC1.bias": "DenseRes1_b0",
    "DenseRes1.FC0.weight": "DenseRes2_w0",
    "DenseRes1.FC0.bias": "DenseRes2_b0",
    "DenseRes1.FC1.weight": "DenseRes3_w0",
    "DenseRes1.FC1.bias": "DenseRes3_b0",
}

with torch.no_grad():
    for name, param in model.named_parameters():
        fp = f"{getbinname[name]}.bin"
        savednp = np.fromfile(fp, dtype=np.float32)
        shape_ = param.shape
        param.copy_(torch.from_numpy(savednp.reshape(shape_, order="C"))) 
        # print(param)
        # print(savednp)

In [7]:
with torch.no_grad():
    for name, param in model.named_parameters():
        print(name, param)

Encoder0.weight Parameter containing:
tensor([[-0.0751, -0.0893,  0.0815,  ..., -0.0023,  0.0108,  0.0553],
        [-0.0455,  0.0524, -0.0306,  ..., -0.0354, -0.0475, -0.0086],
        [-0.0329,  0.0703, -0.0476,  ...,  0.0040,  0.0093, -0.0899],
        ...,
        [ 0.0060,  0.0643, -0.0282,  ...,  0.0184,  0.0319, -0.0253],
        [-0.0182,  0.0615,  0.0271,  ...,  0.0675, -0.0561, -0.0581],
        [-0.0358,  0.0303,  0.0649,  ..., -0.0089,  0.0761, -0.2177]],
       device='cuda:0', requires_grad=True)
Encoder0.bias Parameter containing:
tensor([-0.1640, -0.3014, -0.1578, -0.0544, -0.2442, -0.4230, -0.0730, -0.1455,
        -0.1958, -0.2338, -0.1662, -0.1184, -0.1595, -0.1054, -0.2449, -0.2744,
         0.3854, -0.2818,  0.5248, -0.0677, -0.1090, -0.1178, -0.2102,  0.2377,
         0.4789,  0.1886, -0.2035, -0.2202, -0.3630, -0.1779, -0.1787, -0.0984,
        -0.1555, -0.1249, -0.1549, -0.3549, -0.1839, -0.1523, -0.1989, -0.1677,
        -0.0936, -0.1551, -0.2757, -0.1913, -0.2

In [8]:
Xmean = np.fromfile("Xmean.bin", dtype=np.float32)
Ymean = np.fromfile("Ymean.bin", dtype=np.float32)
print(Xmean.shape, Xmean[-20:])
print(Ymean.shape, Ymean[-20:])

(2350,) [-0.61872  0.44557  0.17121 -0.65208  0.34153  0.36247  0.28213 -0.08111
 -0.28643 -0.33598  0.17554 -0.23346 -0.46493  0.07751 -0.10986 -0.52472
  0.10809  0.13183 -0.62187  0.22497]
(214,) [0.92892 0.77443 0.53388 0.6854  0.53704 0.5237  0.80279 0.66747 0.57714
 0.83595 0.76592 0.66795 0.87527 0.8128  0.73279 0.63066 0.63877 0.80745
 0.79434 0.76837]


In [9]:
loss_fn = nn.MSELoss()
model.to(device)

def test(bindata, model):
    model.eval()
    test_loss, correct = 0, 0
    with torch.no_grad():
        x, y = torch.from_numpy(bindata["Xmean"]), torch.from_numpy(bindata["Ymean"])
        pose = x[:192].to(device).unsqueeze(0)
        traj = x[192:528].to(device).unsqueeze(0)
        sensor = x[528:].to(device).unsqueeze(0)
        y = y.to(device).unsqueeze(0)
        pred = model(pose, traj, sensor)
        test_loss = loss_fn(pred, y)
    
    torch.set_printoptions(threshold=10_000)
    print(f"Input: {x[:16]}")
    print(f"Actual: {y.squeeze(0)[:16]}")
    print(f'Predicted: {pred.squeeze(0)[:16]}')
    print(f"Loss: {test_loss}")

test(bindata, model)

Input: tensor([ 0.0000,  0.0000,  0.0000, -0.2251,  0.1177, -0.0623, -0.4226,  0.2596,
        -0.1927, -0.7172,  0.3679, -0.3507, -1.0464,  0.4562, -0.4728, -1.0769])
Actual: tensor([ 0.0000,  0.0000,  0.0000, -0.2251,  0.1177, -0.0623, -0.4226,  0.2596,
        -0.1927, -0.7172,  0.3679, -0.3507, -1.0464,  0.4563, -0.4728, -1.0769],
       device='cuda:0')
Predicted: tensor([ 0.0005,  0.0005,  0.0005,  0.0005,  0.0005,  0.0005, -0.1027,  0.0645,
        -0.0620, -0.3811,  0.1370,  0.0357, -0.4754, -0.0834,  0.0494,  0.0005],
       device='cuda:0')
Loss: 0.21744012832641602


Pose, Traj, sensor情報のロード

In [15]:
os.chdir('../..')
print(os.getcwd())

/workspace/rendering


In [26]:
from pathlib import Path

hov3_flame_number = 1000
filepaths_pkl = Path("data/HO3D_v3/train/").glob("*/meta/*.pkl")
filepaths_pkl_list = list(filepaths_pkl)
print(filepaths_pkl_list[0:5])
filepaths_bg = Path("data/HO3D_v3/train/").glob("*/rgb/*.jpg")
filepaths_bg_list = list(filepaths_bg)
print(filepaths_bg_list[0:5])

#max 0~20
object_number = 6
filepaths_obj = Path("data/models/").glob("*/textured_simple.obj")
filepaths_obj_list = list(filepaths_obj)
print(filepaths_obj_list[object_number])

[PosixPath('data/HO3D_v3/train/MDF11/meta/0000.pkl'), PosixPath('data/HO3D_v3/train/MDF11/meta/0001.pkl'), PosixPath('data/HO3D_v3/train/MDF11/meta/0002.pkl'), PosixPath('data/HO3D_v3/train/MDF11/meta/0003.pkl'), PosixPath('data/HO3D_v3/train/MDF11/meta/0004.pkl')]
[PosixPath('data/HO3D_v3/train/MDF11/rgb/0000.jpg'), PosixPath('data/HO3D_v3/train/MDF11/rgb/0001.jpg'), PosixPath('data/HO3D_v3/train/MDF11/rgb/0002.jpg'), PosixPath('data/HO3D_v3/train/MDF11/rgb/0003.jpg'), PosixPath('data/HO3D_v3/train/MDF11/rgb/0004.jpg')]
data/models/008_pudding_box/textured_simple.obj


ambient

In [30]:
from utils.mano import ManoLayer
from utils.utils import load_ho_meta, get_obj_mesh, apply_transform_to_mesh, add_trimesh_to_fig
import trimesh
import plotly.graph_objects as go
import trimesh
import numpy as np
import torch
from scipy.spatial.transform import Rotation as R

# load object
obj_mesh = trimesh.load_mesh(filepaths_obj_list[object_number])

mano = ManoLayer()
anno = load_ho_meta(filepaths_pkl_list[hov3_flame_number])

mano_hand = mano(anno)

obj_verts, obj_faces, obj_uv, obj_map = get_obj_mesh(anno)
obj_verts = apply_transform_to_mesh(obj_verts, anno)

mano_mesh = trimesh.Trimesh(vertices=mano_hand.vertices[0], faces=mano.faces, )
obj_mesh = trimesh.Trimesh(vertices=obj_verts, faces=obj_faces)

class AmbientSensor():
    def __init__(self, cell_length=0.018):
        # 3次元格子の生成
        x = np.linspace(0, -cell_length*10, 10) 
        y = np.linspace(0, -cell_length*10, 10)
        z = np.linspace(0, cell_length*10, 10)
        X, Y, Z = np.meshgrid(x, y, z, indexing='ij')
        self.lattice = torch.from_numpy(np.column_stack((X.ravel(), Y.ravel(), Z.ravel()))).to(torch.float32)
        trans = torch.tensor([[0.04,0.0,-0.09]])
        self.lattice += trans
        self.lattice_origin = self.lattice.clone()
        self.values = torch.rand(self.lattice.shape[0])
        self.cell_length = cell_length

    # set transform to mano hand
    def calc_ambient(self, mano_hand, obj_mesh):
        middle_pos = mano_hand.joints[:, 4]#[np.newaxis, :]
        rotvec = mano_hand.global_orient[0]
        rot = torch.from_numpy(R.from_rotvec(rotvec).as_matrix()).to(torch.float32)
        
        self.lattice = self.lattice_origin @ rot.T + middle_pos
        
        # get signed distance from object mesh to lattice
        sd = torch.from_numpy(obj_mesh.nearest.signed_distance(self.lattice)).to(torch.float32)
        
        # calc ambient value
        self.values[sd < (-self.cell_length)] = 0
        self.values[sd > (-self.cell_length)] = 1 - sd[sd > (-self.cell_length)] / self.cell_length
        self.values[sd > 0] = 1
        return self.values


    def get_spheres(self):
        # 3次元格子を描画
        lattice_spheres = [trimesh.primitives.Sphere(radius=0.005, center=point) for point in self.lattice]

amb = AmbientSensor()
amb.calc_ambient(mano_hand, obj_mesh)
# print(amb.values)
print(amb.values.min(), amb.values.max())

fig = go.Figure()
add_trimesh_to_fig(fig, mano_mesh, opacity=0.8)
add_trimesh_to_fig(fig, obj_mesh, opacity=0.8)

fig.add_trace(
    go.Scatter3d(
        x=mano_hand.joints[:, 4, 0],
        y=mano_hand.joints[:, 4, 1],
        z=mano_hand.joints[:, 4, 2],
        mode='markers',
        marker=dict(
            size=5,
            color='red',
            opacity=1
        )
    )
)

fig.add_trace(
    go.Scatter3d(
        x=amb.lattice[:, 0],
        y=amb.lattice[:, 1],
        z=amb.lattice[:, 2],
        mode='markers',
        marker=dict(
            size=2,
            color=amb.values,
            colorscale='Viridis',
            opacity=0.5
        )
    )
)

torch.Size([9174, 3]) torch.Size([3, 3]) torch.Size([3])
tensor(0.) tensor(1.9846)


In [28]:
# input info
print(amb.values)
print(amb.values.shape)

tensor([0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 1.7556, 1.2212, 1.4470, 1.7889, 1.7611, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 1.4456, 1.0000, 1.0000, 1.2520, 1.4055, 1.6029,
        0.0000, 0.0000, 0.0000, 0.0000, 1.6976, 1.3112, 1.2881, 1.3499, 1.3629,
        1.5152, 1.7305, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 1.7162,
        1.7852, 1.8233, 1.9498, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 1.8636, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 1.4804, 

proximity

In [29]:
import plotly.graph_objects as go

def add_mesh(fig, mesh, **kwargs):
    # fig = go.Figure()
    x, y, z = mesh.vertices.T
    i, j, k = mesh.faces.T
    fig.add_trace(
        go.Mesh3d(x=x,y=y,z=z,i=i,j=j,k=k, **kwargs)
    )
    return fig

In [31]:
import numpy as np
import torch

def calc_face_normals(verts, faces):
    v1 = verts[faces[:,0].type(torch.long)]
    v2 = verts[faces[:,1].type(torch.long)]
    v3 = verts[faces[:,2].type(torch.long)]
    face_normals = np.cross(v2-v1, v3-v1)
    face_normals = face_normals / np.linalg.norm(face_normals, axis=1)[:,None]
    return face_normals


def calc_vertex_normals(verts, faces):
    face_normals = calc_face_normals(verts, faces)
    vertex_normals = np.zeros(verts.shape)
    for i, face in enumerate(faces):
        vertex_normals[face] += face_normals[i]
    vertex_normals = vertex_normals / np.linalg.norm(vertex_normals, axis=1)[:,None]
    return vertex_normals

class Proximity():
    def __init__(self):
        # pass
        self.proximity_inds = np.array(
            "228 168  10  74  75 288 379 142 266  64  64   9  62 150 151 132  74  77 \
            74 776 770 275 271 275  63 775 774 152  93  63  69  63 148 147  67 157\
            268  66 775  72  73  73 268  69 148  70 285 607 582 625 682 604 489 496\
            496 470 469 507 565 550 564 141 379 386 358 358 357 397 454 439 453 171\
            194  48  47 238 341 342 329 342 171 704 700 714 760 756 761 763 764 768\
            744 735 745 759 763 683 695 159 157 157  99  27  25  24".split()).astype(int)

    def compute(self, mano_verts, mano_faces, object_mesh, max_distance=0.01):
        self.proximity_verts = mano_verts[0][self.proximity_inds]
        self.proximity_normals = calc_vertex_normals(mano_verts[0], mano_faces)[self.proximity_inds]
        ray_origins = self.proximity_verts.numpy()
        ray_directions = self.proximity_normals

        self.locations, index_ray, index_tri = object_mesh.ray.intersects_location(
            ray_origins=ray_origins, 
            ray_directions=ray_directions,
            multiple_hits=False,
        )

        self.ray_distances = np.linalg.norm(self.locations - ray_origins[index_ray], axis=1)
        self.ray_distances_threashed = np.clip(self.ray_distances, 0, max_distance)
        self.proximity_d = self.proximity_normals.copy()
        self.proximity_d[index_ray] *= self.ray_distances_threashed[:, None] 
        
        self.index_out = np.setdiff1d(np.arange(len(self.proximity_verts)), index_ray)
        self.proximity_d[self.index_out] *= max_distance

        self.index_ray = index_ray
        return self.proximity_verts, self.proximity_d

mano_verts = mano_hand.vertices
mano_faces = mano.faces

proximity = Proximity()
proximity_verts, proximity_dir = proximity.compute(mano_verts, mano_faces, obj_mesh, max_distance=0.1)



In [32]:
fig = go.Figure()
fig = add_mesh(fig, mano_mesh, opacity=1.0)
fig = add_mesh(fig, obj_mesh, opacity=0.8)

fig.add_trace(
    go.Scatter3d(
        x=proximity.locations[:,0], 
        y=proximity.locations[:,1], 
        z=proximity.locations[:,2], 
        mode="markers",
        marker=dict(
            size=2,
            color='blue'
        )
    )
)

proximity_distance = np.linalg.norm(proximity_dir, axis=1)
index_out = proximity.index_out
for i, (v, d, dist) in enumerate(zip(proximity_verts, proximity_dir, proximity_distance)):
    fig.add_trace(
        go.Scatter3d(
            x=[v[0], v[0]+d[0]], 
            y=[v[1], v[1]+d[1]], 
            z=[v[2], v[2]+d[2]], 
            mode="lines",
            line=dict(
                color='yellow' if i in index_out else 'blue', 
                width=3),
            opacity=0.3 if i in index_out else 0.5
        )
    )
fig.show()

In [33]:
# input info
print(proximity.ray_distances_threashed.shape)
print(proximity_distance)
print(proximity_distance.shape)

(75,)
[0.0284661  0.01556218 0.01269791 0.01115199 0.024436   0.01530246
 0.03006273 0.0092228  0.0449264  0.02300432 0.02300432 0.05192508
 0.01786497 0.01634914 0.01559393 0.01542068 0.01115199 0.01055645
 0.01115199 0.00581649 0.0057796  0.01200641 0.01453156 0.01200641
 0.01940679 0.1        0.1        0.01659613 0.0183318  0.01940679
 0.01820872 0.01940679 0.01430428 0.01538799 0.1        0.1
 0.01765905 0.1        0.1        0.1        0.1        0.1
 0.01765905 0.01820872 0.01430428 0.1        0.1        0.05175551
 0.0025672  0.00175425 0.00217889 0.00294069 0.00876954 0.00418024
 0.00418024 0.00131845 0.05849468 0.00288447 0.00551899 0.1
 0.00526879 0.008306   0.03006273 0.03334017 0.03344285 0.03344285
 0.03258481 0.02319046 0.05328983 0.01083909 0.03241519 0.01343425
 0.00474375 0.00609835 0.00564307 0.05331685 0.05663129 0.05502216
 0.04554549 0.05502216 0.01343425 0.00786435 0.1        0.0119182
 0.02087298 0.1        0.02134047 0.1        0.1        0.1
 0.1        0.1   

signed distance

In [34]:
import plotly.graph_objects as go

def add_mesh(fig, mesh, **kwargs):
    # fig = go.Figure()
    x, y, z = mesh.vertices.T
    i, j, k = mesh.faces.T
    fig.add_trace(
        go.Mesh3d(x=x,y=y,z=z,i=i,j=j,k=k, **kwargs)
    )
    return fig

In [35]:
import torch
import trimesh
import numpy as np

def get_another_obj_mesh(anno, name):
    obj_filename = f'data/models/{name}/textured_simple.obj'
    obj_trimesh = trimesh.load_mesh(obj_filename)

    obj_verts = torch.tensor(obj_trimesh.vertices, dtype=torch.float32)
    obj_faces = torch.tensor(obj_trimesh.faces, dtype=torch.int64)
    obj_uv = torch.tensor(obj_trimesh.visual.uv, dtype=torch.float32)
    obj_map = torch.from_numpy(np.array(obj_trimesh.visual.material.image, dtype=np.float32)) / 255.0

    return obj_verts, obj_faces, obj_uv, obj_map

In [57]:
from utils.mano import ManoLayer
from utils.utils import load_ho_meta, get_obj_mesh, apply_transform_to_mesh
import trimesh

# obj_verts, obj_faces, obj_uv, obj_map = get_another_obj_mesh(anno, "025_mug")
# obj_verts = apply_transform_to_mesh(obj_verts, anno)

handjoints = anno['handJoints3D']
print(anno['handTrans'].shape)
print(handjoints, handjoints.shape)


(3,)
[[-1.84181298e-01  7.87092891e-02 -7.67031608e-01]
 [-1.14829468e-01  4.22186296e-02 -7.10624694e-01]
 [-8.82577320e-02  1.65370185e-02 -7.06464945e-01]
 [-7.87357111e-02 -2.42128985e-03 -7.19490944e-01]
 [-1.33025253e-01  2.76070428e-02 -6.97466491e-01]
 [-1.22984650e-01  2.01402258e-02 -6.65457128e-01]
 [-1.11928971e-01  5.63003150e-04 -6.53674481e-01]
 [-1.78474778e-01  1.06420482e-02 -7.17903730e-01]
 [-1.74386972e-01 -5.83934051e-03 -7.02146765e-01]
 [-1.66394198e-01 -2.25792821e-02 -6.92691084e-01]
 [-1.59867549e-01  1.86472948e-02 -7.06122634e-01]
 [-1.48279840e-01 -7.90737617e-03 -6.93954465e-01]
 [-1.41647571e-01 -3.53982891e-02 -6.94354232e-01]
 [-1.46343763e-01  6.70852286e-02 -7.67882525e-01]
 [-1.23952257e-01  4.27866054e-02 -7.72838770e-01]
 [-1.18475857e-01  1.37155574e-02 -7.76712892e-01]
 [-1.14637347e-01 -2.50750187e-02 -7.79835400e-01]
 [-7.92718697e-02 -1.63928642e-02 -7.43874190e-01]
 [-1.01391973e-01 -2.61251191e-02 -6.54116211e-01]
 [-1.38603383e-01 -6.04063

In [37]:
import numpy as np
import torch

def calc_face_normals(verts, faces):
    v1 = verts[faces[:,0].type(torch.long)]
    v2 = verts[faces[:,1].type(torch.long)]
    v3 = verts[faces[:,2].type(torch.long)]
    face_normals = np.cross(v2-v1, v3-v1)
    face_normals = face_normals / np.linalg.norm(face_normals, axis=1)[:,None]
    return face_normals

print(calc_face_normals(obj_verts, obj_faces))
print(obj_mesh.face_normals)


[[-0.1551232   0.9813118   0.11385925]
 [-0.14756778  0.981224    0.12418976]
 [ 0.79572767  0.5978896   0.0966724 ]
 ...
 [-0.3242809   0.394738   -0.859665  ]
 [-0.1448486   0.6440898  -0.7511107 ]
 [-0.21879652  0.90088934 -0.3748686 ]]
[[-0.15512321  0.98131181  0.11385926]
 [-0.14756778  0.98122406  0.12418976]
 [ 0.79572766  0.59788957  0.09667242]
 ...
 [-0.32428088  0.39473797 -0.85966496]
 [-0.14484859  0.64408979 -0.75111066]
 [-0.21879653  0.90088933 -0.37486864]]


In [38]:
def calc_vertex_normals(verts, faces):
    face_normals = calc_face_normals(verts, faces)
    vertex_normals = np.zeros(verts.shape)
    for i, face in enumerate(faces):
        vertex_normals[face] += face_normals[i]
    vertex_normals = vertex_normals / np.linalg.norm(vertex_normals, axis=1)[:,None]
    return vertex_normals

print(calc_vertex_normals(obj_verts, obj_faces))
print(obj_mesh.vertex_normals)

[[ 0.94783003 -0.15065525  0.28092921]
 [ 0.34243182  0.93364617  0.10509654]
 [ 0.80471266  0.35835989 -0.47330299]
 ...
 [-0.18914911  0.48633665 -0.85305292]
 [-0.30832092  0.37299989 -0.8751053 ]
 [-0.06472686 -0.00889747 -0.99786335]]
[[ 0.94845161 -0.15209978  0.27803814]
 [ 0.06226486  0.99586473  0.06615536]
 [ 0.80624823  0.35784893 -0.47107104]
 ...
 [-0.18264417  0.50502191 -0.8435603 ]
 [-0.30938605  0.36345017 -0.87874015]
 [-0.06623846 -0.03851411 -0.99706024]]


In [43]:
class SinedDistanceNormals:
    def __init__(self):
        pass

    def calc_sd_normals(self, obj_mesh, handjoints):
        closest, distance, triangle_id = trimesh.proximity.closest_point(obj_mesh, handjoints)
        
        obj_verts = torch.tensor(obj_mesh.vertices)
        obj_faces = torch.tensor(obj_mesh.faces)
        face_normals = calc_face_normals(obj_verts, obj_faces)
        closest_normals = face_normals[triangle_id]
        sd_normals = closest_normals * distance[:,None]

        self.closest = closest
        self.distance = distance
        self.closest_normals = closest_normals
        self._sd_normals = sd_normals
        return sd_normals

sd = SinedDistanceNormals()
sd_normals = sd.calc_sd_normals(obj_mesh, handjoints)

In [44]:
#input info
print(sd.distance, sd.distance.shape)
print(sd_normals, sd_normals.shape)

[0.07362045 0.02672153 0.01655093 0.00205408 0.02449312 0.04065956
 0.0285828  0.00644469 0.00522164 0.0070144  0.01626301 0.0089548
 0.00645439 0.04685029 0.02534931 0.01217082 0.01814158 0.00364576
 0.0061619  0.02258354 0.01811181] (21,)
[[-3.44485753e-02  4.81821234e-02 -4.37235477e-02]
 [-5.11727243e-03  1.85591388e-02  1.85313778e-02]
 [ 1.32120698e-02  6.06569677e-03  7.91086060e-03]
 [ 1.16567792e-03 -6.50004222e-04  1.56138612e-03]
 [-1.44342306e-02  1.97185512e-02  1.65668103e-03]
 [-3.97446759e-03  3.64064276e-02  1.76628264e-02]
 [ 2.22144069e-04  2.42365463e-02  1.51498115e-02]
 [-1.45140305e-03  6.27151871e-03  3.09065890e-04]
 [-3.33992338e-04  1.55271027e-03  4.97423805e-03]
 [-2.69931938e-03 -1.15503272e-03  6.37035642e-03]
 [-1.00353606e-02  5.02099316e-03  1.17714309e-02]
 [ 6.71571453e-05  6.04240476e-03  6.60857932e-03]
 [-6.17857668e-03 -1.80903892e-03  4.60108527e-04]
 [-1.87980694e-02  3.44670038e-02 -2.55657568e-02]
 [-9.28014825e-03  1.78599964e-02 -1.54106160

In [40]:
fig = go.Figure()
add_mesh(fig, mano_mesh, opacity=1.0)
add_mesh(fig, obj_mesh, opacity=0.5)
fig.add_trace(go.Scatter3d(x=handjoints[:,0], y=handjoints[:,1], z=handjoints[:,2], mode='markers', marker=dict(size=5), name='handjoints'))
fig.add_trace(
    go.Scatter3d(
        x=sd.closest[:,0], 
        y=sd.closest[:,1], z=sd.closest[:,2], mode='markers', marker=dict(size=5)
        )
    )

for p1, p2 in zip(handjoints, sd.closest):
    fig.add_trace(
        go.Scatter3d(
            x=[p1[0], p2[0]], y=[p1[1], p2[1]], z=[p1[2], p2[2]], 
            mode='lines', line=dict(width=3, color='orange'),
            name='closest'
        )
        )

for p, n in zip(sd.closest, sd_normals):
    fig.add_trace(
        go.Scatter3d(
            x=[p[0], p[0]+n[0]], y=[p[1], p[1]+n[1]], z=[p[2], p[2]+n[2]], 
            mode='lines', line=dict(width=3, color='cyan'),
            name='sd_normals'
        )
        )

fig.show()

input infomation into Network

In [71]:
#pose

pos_tensor = torch.flatten(torch.from_numpy(handjoints))
print(pos_tensor.shape)

# ?????
rot = anno['handTrans']
rot_list = []
for i in range(2 * 21):
    rot_list.append(rot)
rot_tensor = torch.flatten(torch.tensor(rot_list))
print(rot_tensor.shape)

pose_tensor = torch.cat([pos_tensor, rot_tensor], dim=0)
print(pose_tensor.shape)

# この入力がわかりません

torch.Size([63])
torch.Size([126])
torch.Size([189])


In [79]:
# traj

#rootのposとrotを入れたい
traj_r_pos = torch.tensor(anno['handJoints3D'][0])
# わからない、本来６次元
traj_r_rot = torch.tensor(anno['handTrans'])
print(traj_r_pos, traj_r_rot)

pos_list = []
rot_list = []
for i in range(21):
    pos_list.append(traj_r_pos)
    rot_list.append(traj_r_rot)
traj_r_pos_concat = torch.cat(pos_list)
traj_r_rot_concat = torch.cat(rot_list)
print(traj_r_pos_concat.shape)
print(traj_r_rot_concat.shape)
traj_right_tensor = torch.cat([traj_r_pos_concat, traj_r_rot_concat], dim=0)
print(traj_right_tensor.shape)

#left



tensor([-0.1842,  0.0787, -0.7670], dtype=torch.float64) tensor([-0.2863,  0.0725, -0.7737])
torch.Size([63])
torch.Size([63])
torch.Size([126])


In [55]:
amb_tensor = amb.values

pro = torch.from_numpy(proximity_distance)
proxi_tensor = torch.cat([pro, pro, pro, pro, pro, pro], dim=0)

dis = torch.from_numpy(sd.distance)
sd_distance_tensor = torch.cat([dis, dis, dis, dis, dis, dis])
sd_normals_tensor = torch.flatten(torch.from_numpy(sd_normals))
sd_tensor = torch.cat([sd_distance_tensor, sd_normals_tensor], dim=0)
sensor_tensor = torch.cat([amb_tensor, proxi_tensor, sd_tensor], dim=0)
# 1822 
print(sensor_tensor.shape)

# joints？が21しかないので、数が合わないです。

torch.Size([1813])


In [ ]:
# これは、上のロスを求める関数そのままです。
loss_fn = nn.MSELoss()
model.to(device)

def test(bindata, model):
    model.eval()
    test_loss, correct = 0, 0
    with torch.no_grad():
        x, y = torch.from_numpy(bindata["Xmean"]), torch.from_numpy(bindata["Ymean"])
        pose = x[:192].to(device).unsqueeze(0)
        traj = x[192:528].to(device).unsqueeze(0)
        sensor = x[528:].to(device).unsqueeze(0)
        y = y.to(device).unsqueeze(0)
        pred = model(pose, traj, sensor)
        test_loss = loss_fn(pred, y)
    
    torch.set_printoptions(threshold=10_000)
    print(f"Input: {x[:16]}")
    print(f"Actual: {y.squeeze(0)[:16]}")
    print(f'Predicted: {pred.squeeze(0)[:16]}')
    print(f"Loss: {test_loss}")

test(bindata, model)